In [ ]:
"""
The majority of this kernel references the work of another Kaggle user. 
Here, I've mainly organized the code and adjusted the parameters. 
If you'd like to view the original author's code, please visit their page and give them a thumbs-up.

Reference : https://www.kaggle.com/code/yeoyunsianggeremie/private-lb-9-61-s3e20-kmeans-lightgbm?scriptVersionId=140627992
"""

In [1]:
import pandas as pd
import numpy as np
import os
import matplotlib.pyplot as plt

from sklearn.model_selection import train_test_split
pd.options.display.float_format = '{:.5}'.format #小數點後保留5位
pd.options.display.max_rows = None

%matplotlib inline
import warnings
warnings.filterwarnings('ignore') # You can ignore the Shapely GEOS warning :-)

In [2]:
!pip install haversine

In [3]:
DATA_PATH = 'D:/kaggle/input4'
#Load files
train = pd.read_csv(os.path.join(DATA_PATH, 'train.csv'))
test = pd.read_csv(os.path.join(DATA_PATH, 'test.csv'))
samplesubmission = pd.read_csv(os.path.join(DATA_PATH, 'sample_submission.csv'))

#Preview train dataset
train.head()

ID_LAT_LON_YEAR_WEEK  latitude  longitude  year  week_no  \
0  ID_-0.510_29.290_2019_00     -0.51      29.29  2019        0   
1  ID_-0.510_29.290_2019_01     -0.51      29.29  2019        1   
2  ID_-0.510_29.290_2019_02     -0.51      29.29  2019        2   
3  ID_-0.510_29.290_2019_03     -0.51      29.29  2019        3   
4  ID_-0.510_29.290_2019_04     -0.51      29.29  2019        4   

   SulphurDioxide_SO2_column_number_density  \
0                               -0.00010834   
1                                2.0527e-05   
2                                0.00051414   
3                                       NaN   
4                               -7.8766e-05   

   SulphurDioxide_SO2_column_number_density_amf  \
0                                       0.60302   
1                                       0.72821   
2                                        0.7482   
3                                           NaN   
4                                        0.6763   

   SulphurDioxide_SO2_slant_column_number_density  \
0                                     -6.5331e-05   
1                                       1.361e-05   
2                                      0.00038468   
3                                             NaN   
4                                     -4.7624e-05   

   SulphurDioxide_cloud_fraction  SulphurDioxide_sensor_azimuth_angle  ...  \
0                        0.25567                              -98.594  ...   
1                        0.13099                               16.593  ...   
2                        0.11002                               72.796  ...   
3                            NaN                                  NaN  ...   
4                        0.12116                               4.1213  ...   

   Cloud_cloud_top_height  Cloud_cloud_base_pressure  Cloud_cloud_base_height  \
0                  3664.4                 6.1086e+04                   2615.1   
1                  3651.2                 6.6969e+04                   3174.6   
2                  4217.0                 6.0069e+04                   3516.3   
3                  5228.5                 5.1065e+04                   4181.0   
4                  3980.6                 6.3751e+04                   3355.7   

   Cloud_cloud_optical_depth  Cloud_surface_albedo  \
0                     15.569               0.27229   
1                     8.6906               0.25683   
2                     21.103                0.2511   
3                     15.387               0.26204   
4                     8.1147               0.23585   

   Cloud_sensor_azimuth_angle  Cloud_sensor_zenith_angle  \
0                     -12.629                     35.632   
1                      30.359                     39.558   
2                      15.378                     30.402   
3                     -11.293                      24.38   
4                      38.532                     37.393   

   Cloud_solar_azimuth_angle  Cloud_solar_zenith_angle  emission  
0                    -138.79                    30.752     3.751  
1                    -145.18                    27.252    4.0252  
2                    -142.52                    26.193    4.2314  
3                    -132.67                    28.829    4.3053  
4                    -141.51                    22.205    4.3473  

[5 rows x 76 columns]

In [4]:
train = train[["latitude", "longitude", "year", "week_no", "emission"]].fillna(0)
test = test[["ID_LAT_LON_YEAR_WEEK","latitude", "longitude", "year", "week_no",]].fillna(0) 

In [5]:
#https://www.kaggle.com/code/lucasboesen/simple-catboost-6-features-cv-21-7
from sklearn.cluster import KMeans
import haversine as hs

km_train = train.groupby(by=['latitude', 'longitude'], as_index=False)['emission'].mean()
model = KMeans(n_clusters = 7, random_state = 42)
model.fit(km_train)
yhat_train = model.predict(km_train)
km_train['kmeans_group'] = yhat_train

""" Own Groups """
# Some locations have emission == 0
km_train['is_zero'] = km_train['emission'].apply(lambda x: 'no_emission_recorded' if x==0 else 'emission_recorded')

# Distance to the highest emission location
max_lat_lon_emission = km_train.loc[km_train['emission']==km_train['emission'].max(), ['latitude', 'longitude']]
km_train['distance_to_max_emission'] = km_train.apply(lambda x: hs.haversine((x['latitude'], x['longitude']), (max_lat_lon_emission['latitude'].values[0], max_lat_lon_emission['longitude'].values[0])), axis=1)

train = train.merge(km_train[['latitude', 'longitude', 'kmeans_group', 'distance_to_max_emission']], on=['latitude', 'longitude'])
test = test.merge(km_train[['latitude', 'longitude', 'kmeans_group', 'distance_to_max_emission']], on=['latitude', 'longitude'])
#train = train.drop(columns = ["latitude", "longitude"])
#test = test.drop(columns = ["latitude", "longitude"])

In [6]:
train.head()

latitude  longitude  year  week_no  emission  kmeans_group  \
0     -0.51      29.29  2019        0     3.751             0   
1     -0.51      29.29  2019        1    4.0252             0   
2     -0.51      29.29  2019        2    4.2314             0   
3     -0.51      29.29  2019        3    4.3053             0   
4     -0.51      29.29  2019        4    4.3473             0   

   distance_to_max_emission  
0                    207.85  
1                    207.85  
2                    207.85  
3                    207.85  
4                    207.85

In [7]:
train["kmeans_group"].value_counts()

0    31482
6    20193
4    15900
1     8427
5     2703
3      159
2      159
Name: kmeans_group, dtype: int64

In [8]:
test.head()

ID_LAT_LON_YEAR_WEEK  latitude  longitude  year  week_no  kmeans_group  \
0  ID_-0.510_29.290_2022_00     -0.51      29.29  2022        0             0   
1  ID_-0.510_29.290_2022_01     -0.51      29.29  2022        1             0   
2  ID_-0.510_29.290_2022_02     -0.51      29.29  2022        2             0   
3  ID_-0.510_29.290_2022_03     -0.51      29.29  2022        3             0   
4  ID_-0.510_29.290_2022_04     -0.51      29.29  2022        4             0   

   distance_to_max_emission  
0                    207.85  
1                    207.85  
2                    207.85  
3                    207.85  
4                    207.85

In [9]:
train.latitude, train.longtitude = round(train.latitude, 2), round(train.longitude, 2)

In [10]:
#首先創造一個unique的經緯度，就是train再額外加一個欄叫做'location'.
train['location'] = [str(x) + '_' + str(y) for x, y in zip(train.latitude, train.longitude)]

In [11]:
train.head()

latitude  longitude  year  week_no  emission  kmeans_group  \
0     -0.51      29.29  2019        0     3.751             0   
1     -0.51      29.29  2019        1    4.0252             0   
2     -0.51      29.29  2019        2    4.2314             0   
3     -0.51      29.29  2019        3    4.3053             0   
4     -0.51      29.29  2019        4    4.3473             0   

   distance_to_max_emission     location  
0                    207.85  -0.51_29.29  
1                    207.85  -0.51_29.29  
2                    207.85  -0.51_29.29  
3                    207.85  -0.51_29.29  
4                    207.85  -0.51_29.29

In [12]:
train.drop(columns = ["emission"]).head() # X

latitude  longitude  year  week_no  kmeans_group  distance_to_max_emission  \
0     -0.51      29.29  2019        0             0                    207.85   
1     -0.51      29.29  2019        1             0                    207.85   
2     -0.51      29.29  2019        2             0                    207.85   
3     -0.51      29.29  2019        3             0                    207.85   
4     -0.51      29.29  2019        4             0                    207.85   

      location  
0  -0.51_29.29  
1  -0.51_29.29  
2  -0.51_29.29  
3  -0.51_29.29  
4  -0.51_29.29

In [13]:
train["emission"].head() #y

0    3.751
1   4.0252
2   4.2314
3   4.3053
4   4.3473
Name: emission, dtype: float64

In [14]:
test['location'] = [str(x) + '_' + str(y) for x, y in zip(test.latitude, test.longitude)]

In [15]:
test.head()

ID_LAT_LON_YEAR_WEEK  latitude  longitude  year  week_no  kmeans_group  \
0  ID_-0.510_29.290_2022_00     -0.51      29.29  2022        0             0   
1  ID_-0.510_29.290_2022_01     -0.51      29.29  2022        1             0   
2  ID_-0.510_29.290_2022_02     -0.51      29.29  2022        2             0   
3  ID_-0.510_29.290_2022_03     -0.51      29.29  2022        3             0   
4  ID_-0.510_29.290_2022_04     -0.51      29.29  2022        4             0   

   distance_to_max_emission     location  
0                    207.85  -0.51_29.29  
1                    207.85  -0.51_29.29  
2                    207.85  -0.51_29.29  
3                    207.85  -0.51_29.29  
4                    207.85  -0.51_29.29

In [37]:
for km_class in range(7):
    print("Number of group in kmeans class" , km_class , " is " ,len(train.loc[train["kmeans_group"] == km_class]))

Number of group in kmeans class 0  is  31482
Number of group in kmeans class 1  is  8427
Number of group in kmeans class 2  is  159
Number of group in kmeans class 3  is  159
Number of group in kmeans class 4  is  15900
Number of group in kmeans class 5  is  2703
Number of group in kmeans class 6  is  20193


In [20]:
!pip install catboost

In [21]:
from sklearn.utils import shuffle
import catboost as cb

Test = test.drop(columns = ["location","ID_LAT_LON_YEAR_WEEK"]).values
X = train.drop(columns = ["emission","location"]).values
y = train["emission"].values
X, y = shuffle(X, y, random_state=13)
#X = X.astype(np.float32)

offset = int(X.shape[0] * 0.9)

X_train, y_train = X[:offset], y[:offset]
X_test, y_test = X[offset:], y[offset:]


In [22]:
train.head()

latitude  longitude  year  week_no  emission  kmeans_group  \
0     -0.51      29.29  2019        0     3.751             0   
1     -0.51      29.29  2019        1    4.0252             0   
2     -0.51      29.29  2019        2    4.2314             0   
3     -0.51      29.29  2019        3    4.3053             0   
4     -0.51      29.29  2019        4    4.3473             0   

   distance_to_max_emission     location  
0                    207.85  -0.51_29.29  
1                    207.85  -0.51_29.29  
2                    207.85  -0.51_29.29  
3                    207.85  -0.51_29.29  
4                    207.85  -0.51_29.29

In [23]:
train.drop(columns = ["emission","location"]).head()

latitude  longitude  year  week_no  kmeans_group  distance_to_max_emission
0     -0.51      29.29  2019        0             0                    207.85
1     -0.51      29.29  2019        1             0                    207.85
2     -0.51      29.29  2019        2             0                    207.85
3     -0.51      29.29  2019        3             0                    207.85
4     -0.51      29.29  2019        4             0                    207.85

In [24]:
param_grid = {
    'n_estimators': [799],  
    'learning_rate': [0.09180872710592884],
    'depth': [8],
    'l2_leaf_reg': [1.0242996861886846],
    'subsample': [0.38227256755249117],
    'colsample_bylevel': [0.7183481537623551],
    'random_state': [42],
    'silent': [True],
    'feature_weights': [[1.0, 1.0, 1.0, 1.0, x, y] for x in range(1,5) for y in range(5)
]
}
#[[1.0, 1.0, 1.0, 1.0, i, 1.0] for i in range(10)]


In [25]:
from catboost import CatBoostRegressor

In [ ]:
"""
Gridsearch is very time consuming, you can just skip this cell and use best_params directly in next cell.
"""
from sklearn.model_selection import GridSearchCV
mode1_g = CatBoostRegressor()
grid_search = GridSearchCV(mode1_g, param_grid, cv=5, scoring='neg_mean_squared_error', verbose=2)
grid_search.fit(X_train, y_train)
best_params = grid_search.best_params_
print("最佳参数:", best_params)

Fitting 5 folds for each of 20 candidates, totalling 100 fits


In [26]:
# Use best best_params to train the model.
best_params = {'colsample_bylevel': 0.7183481537623551, 'depth': 8, 'feature_weights': [1.0, 1.0, 1.0, 1.0, 3, 1], 'l2_leaf_reg': 1.0242996861886846, 'learning_rate': 0.09180872710592884, 'n_estimators': 799, 'random_state': 42, 'silent': True, 'subsample': 0.38227256755249117}

best_model = CatBoostRegressor(**best_params)
best_model.fit(X_train, y_train, eval_set=(X_test, y_test), verbose=0, plot=True)
"""
最佳参数: {'colsample_bylevel': 0.7183481537623551, 'depth': 8, 'feature_weights': [1.0, 1.0, 1.0, 1.0, 3, 1], 'l2_leaf_reg': 1.0242996861886846, 'learning_rate': 0.09180872710592884, 'n_estimators': 799, 'random_state': 42, 'silent': True, 'subsample': 0.38227256755249117}
"""

MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))

"\n最佳参数: {'colsample_bylevel': 0.7183481537623551, 'depth': 8, 'feature_weights': [1.0, 1.0, 1.0, 1.0, 3, 1], 'l2_leaf_reg': 1.0242996861886846, 'learning_rate': 0.09180872710592884, 'n_estimators': 799, 'random_state': 42, 'silent': True, 'subsample': 0.38227256755249117}\n"

In [27]:
pred_best = best_model.predict(X_test)
print(pred_best)
mse = ((y_test - pred_best)**2).mean(axis=0)
print("mse = ",mse)

[ 16.58506244  20.56502611 142.49837626 ...  77.26454194 185.08938263
  46.59690197]
mse =  104.10891971767873


In [28]:
Test_pred = best_model.predict(Test)

In [29]:
# Transfer Test_pred into DataFrame data type
df_Test_pred = pd.DataFrame(Test_pred) 

In [30]:
# Check if length of submission file is true.
df_Test_pred[0].shape

(24353,)

In [31]:
# Create a submission file
sub_file = pd.DataFrame({'ID_LAT_LON_YEAR_WEEK': test.ID_LAT_LON_YEAR_WEEK, 'emission': df_Test_pred[0]})
sub_file.head()

ID_LAT_LON_YEAR_WEEK  emission
0  ID_-0.510_29.290_2022_00    2.2347
1  ID_-0.510_29.290_2022_01     3.413
2  ID_-0.510_29.290_2022_02    3.6326
3  ID_-0.510_29.290_2022_03    3.7919
4  ID_-0.510_29.290_2022_04    4.1363

In [32]:
sub_file.to_csv(os.path.join(DATA_PATH,'my_data.csv'), index=False)

In [33]:
pd.read_csv(os.path.join(DATA_PATH,'my_data.csv'))

ID_LAT_LON_YEAR_WEEK   emission
0      ID_-0.510_29.290_2022_00     2.2347
1      ID_-0.510_29.290_2022_01      3.413
2      ID_-0.510_29.290_2022_02     3.6326
3      ID_-0.510_29.290_2022_03     3.7919
4      ID_-0.510_29.290_2022_04     4.1363
5      ID_-0.510_29.290_2022_05     4.1714
6      ID_-0.510_29.290_2022_06     4.1292
7      ID_-0.510_29.290_2022_07      4.107
8      ID_-0.510_29.290_2022_08      4.107
9      ID_-0.510_29.290_2022_09      3.126
10     ID_-0.510_29.290_2022_10     4.4973
11     ID_-0.510_29.290_2022_11     4.6251
12     ID_-0.510_29.290_2022_12     4.2862
13     ID_-0.510_29.290_2022_13     3.2851
14     ID_-0.510_29.290_2022_14      4.037
15     ID_-0.510_29.290_2022_15     4.0954
16     ID_-0.510_29.290_2022_16     4.1812
17     ID_-0.510_29.290_2022_17     4.5256
18     ID_-0.510_29.290_2022_18     4.9131
19     ID_-0.510_29.290_2022_19     4.8787
20     ID_-0.510_29.290_2022_20     4.7991
21     ID_-0.510_29.290_2022_21      4.958
22     ID_-0.510_29.290_2022_22     4.9365
23     ID_-0.510_29.290_2022_23     4.5013
24     ID_-0.510_29.290_2022_24     4.5489
25     ID_-0.510_29.290_2022_25     4.4172
26     ID_-0.510_29.290_2022_26     4.3996
27     ID_-0.510_29.290_2022_27     4.2349
28     ID_-0.510_29.290_2022_28     4.2349
29     ID_-0.510_29.290_2022_29     4.1737
30     ID_-0.510_29.290_2022_30     4.0075
31     ID_-0.510_29.290_2022_31       4.35
32     ID_-0.510_29.290_2022_32       4.35
33     ID_-0.510_29.290_2022_33      4.346
34     ID_-0.510_29.290_2022_34     4.5534
35     ID_-0.510_29.290_2022_35     4.8291
36     ID_-0.510_29.290_2022_36     4.9581
37     ID_-0.510_29.290_2022_37     5.3559
38     ID_-0.510_29.290_2022_38     5.6324
39     ID_-0.510_29.290_2022_39     5.2314
40     ID_-0.510_29.290_2022_40     4.2651
41     ID_-0.510_29.290_2022_41     4.1767
42     ID_-0.510_29.290_2022_42     4.2822
43     ID_-0.510_29.290_2022_43     4.3735
44     ID_-0.510_29.290_2022_44     4.6612
45     ID_-0.510_29.290_2022_45     4.6416
46     ID_-0.510_29.290_2022_46     4.6883
47     ID_-0.510_29.290_2022_47     4.8688
48     ID_-0.510_29.290_2022_48     4.6269
49     ID_-0.528_29.472_2022_00    0.97829
50     ID_-0.528_29.472_2022_01     2.1597
51     ID_-0.528_29.472_2022_02     2.3793
52     ID_-0.528_29.472_2022_03     2.5386
53     ID_-0.528_29.472_2022_04      2.883
54     ID_-0.528_29.472_2022_05     2.9181
55     ID_-0.528_29.472_2022_06      2.876
56     ID_-0.528_29.472_2022_07     2.8538
57     ID_-0.528_29.472_2022_08     2.8538
58     ID_-0.528_29.472_2022_09     1.9661
59     ID_-0.528_29.472_2022_10     3.3024
60     ID_-0.528_29.472_2022_11     3.4303
61     ID_-0.528_29.472_2022_12     3.0914
62     ID_-0.528_29.472_2022_13     2.6142
63     ID_-0.528_29.472_2022_14     3.1791
64     ID_-0.528_29.472_2022_15     3.2375
65     ID_-0.528_29.472_2022_16     3.3233
66     ID_-0.528_29.472_2022_17     3.5499
67     ID_-0.528_29.472_2022_18     3.9716
68     ID_-0.528_29.472_2022_19     3.9373
69     ID_-0.528_29.472_2022_20     3.8577
70     ID_-0.528_29.472_2022_21     4.0166
71     ID_-0.528_29.472_2022_22     3.9951
72     ID_-0.528_29.472_2022_23     3.5599
73     ID_-0.528_29.472_2022_24     3.6054
74     ID_-0.528_29.472_2022_25     3.4737
75     ID_-0.528_29.472_2022_26     3.4561
76     ID_-0.528_29.472_2022_27     3.2914
77     ID_-0.528_29.472_2022_28     3.2914
78     ID_-0.528_29.472_2022_29     3.2301
79     ID_-0.528_29.472_2022_30     3.0639
80     ID_-0.528_29.472_2022_31     3.4064
81     ID_-0.528_29.472_2022_32     3.4064
82     ID_-0.528_29.472_2022_33     3.4024
83     ID_-0.528_29.472_2022_34     3.6099
84     ID_-0.528_29.472_2022_35     3.8855
85     ID_-0.528_29.472_2022_36     3.9046
86     ID_-0.528_29.472_2022_37     4.3024
87     ID_-0.528_29.472_2022_38     4.5789
88     ID_-0.528_29.472_2022_39     4.1985
89     ID_-0.528_29.472_2022_40     3.1874
90     ID_-0.528_29.472_2022_41      3.099
91     ID_-0.528_29.472_2022_42     3.2046
92     ID_-0